## 1 Create a Database

We are going to create a database with with three datasets to efficiently access information

To do this, we will need the following imports

In [1]:
import pandas as pd
import numpy as np
import sqlite3

### Temperatures table

The temperatures dataset includes the temperatures for each month of a year for thousands of stations. There is separate file for each decade worth of years, so we add that decade to the url. Let's look at the data table for the most recent decade.

In [3]:
interval = "2011-2020"
temps_url = f"https://raw.githubusercontent.com/PhilChodrow/PIC16B/master/datasets/noaa-ghcn/decades/{interval}.csv"
temperatures = pd.read_csv(temps_url)
temperatures.head(3)

ID  Year  VALUE1  VALUE2  VALUE3  VALUE4  VALUE5  VALUE6  VALUE7  \
0  ACW00011604  2011   -83.0  -132.0   278.0  1040.0  1213.0  1663.0  1875.0   
1  ACW00011604  2012   121.0   -98.0   592.0   646.0  1365.0  1426.0  1771.0   
2  ACW00011604  2013  -104.0   -93.0   -48.0   595.0     NaN  1612.0  1855.0   

   VALUE8  VALUE9  VALUE10  VALUE11  VALUE12  
0  1723.0  1466.0    987.0    721.0    428.0  
1  1748.0  1362.0    826.0    620.0   -234.0  
2  1802.0  1359.0   1042.0    601.0      NaN

The way this data is set up is not tidy, since there are 12 temperatures values in each observation. To make it tidy, we want to have one row for each month. The temperature values are also in hundreths of a degree, so we want to divide them by degree. Let's make a function to do this.

In [23]:
def prep_temp_df(df):
    """
    This function tidys and cleans the data.
    It makes each observation be the temperature for a station, year, and month
    and neatens the new columns of month and temp
    
    Input: df - a dataframe of temperatures
    
    Outputs a restructured dataframe of the temperatures
    """
    #We want to keep ID and Year as columns in the transformed table
    df = df.set_index(keys=["ID", "Year"])
    
    #Convert table
    df = df.stack()
    df = df.reset_index()
    
    #Make the new columns for Month and Temp look nice
    df = df.rename(columns = {"level_2"  : "Month" , 0 : "Temp"})
    df["Month"] = df["Month"].str[5:].astype(int)
    df["Temp"]  = df["Temp"] / 100
    return(df)

Now we want to create a database.

In [56]:
conn = sqlite3.connect("climate.db")

Now we want to add the data, one decade file at a time. So for each decade, we will read in data from the url, prepare it, and add it to the temperatures table.

In [57]:
#List with the start of each decade
decades = np.arange(1901, 2021, 10)

for start in decades:
    interval = str(start) + "-" + str(start+9)
    temps_url = f"https://raw.githubusercontent.com/PhilChodrow/PIC16B/master/datasets/noaa-ghcn/decades/{interval}.csv"
    
    #Create iterator to reach in chunk
    df_iter = pd.read_csv(temps_url, chunksize = 100000)
    
    #Iterate through the file, adding chunks
    for df in df_iter:
        cleaned = prep_temp_df(df)
        cleaned.to_sql("temperatures", conn, if_exists = "append", index = False)

### Stations table

Now we will get our next table from its url.

In [10]:
stations_url = "https://raw.githubusercontent.com/PhilChodrow/PIC16B/master/datasets/noaa-ghcn/station-metadata.csv"
stations = pd.read_csv(stations_url)
stations.head(3)

ID  LATITUDE  LONGITUDE  STNELEV                 NAME
0  ACW00011604   57.7667    11.8667     18.0                 SAVE
1  AE000041196   25.3330    55.5170     34.0   SHARJAH_INTER_AIRP
2  AEM00041184   25.6170    55.9330     31.0  RAS_AL_KHAIMAH_INTE

We will want to use this table to match countries. It turns out the first two characters of the ID match the FIPS 10-4 country code, so let's add that to our table

In [11]:
stations["FIPS"] = stations["ID"].str[0:2]

Now we can add this table directly to the database

In [58]:
stations.to_sql("stations", conn, if_exists = "replace", index = False)

### Countries table

Lastly we are going to add our countries table. We can get it from the url below.

In [14]:
countries_url = "https://raw.githubusercontent.com/mysociety/gaze/master/data/fips-10-4-to-iso-country-codes.csv"
countries = pd.read_csv(countries_url)
countries.head(3)

FIPS 10-4 ISO 3166         Name
0        AF       AF  Afghanistan
1        AX        -     Akrotiri
2        AL       AL      Albania

We are going to run into problems with SQL if the column names have spaces, so let's shorten those. It might also make sense to change Name to Country.

In [15]:
countries = countries.rename(columns = {"FIPS 10-4":"FIPS", "ISO 3166":"ISO", "Name":"Country"})
countries.head(3)

FIPS ISO      Country
0   AF  AF  Afghanistan
1   AX   -     Akrotiri
2   AL  AL      Albania

Then we can add this table to our database

In [59]:
countries.to_sql("countries", conn, if_exists = "replace", index = False)

Since we are done adding to our database, we need to close the connection.

In [60]:
conn.close()

## 2 Write a Query Function

Now we are going to write a function that will create table from the database using SQL

We want to look at temperatures for a given countries for a given month in a range of years. We want the dataframe to have columns for the station name, latititude, longitude, and country, as well as year, month, and temperature of the reading.   

To get this we will make a command. The command will select all of the columns from the abreviated name of table they came from. It will join the temperatures table with station, on id, and countries, on FIPS in order to do this. In the WHERE statement, we will include the conditions.

In [2]:
def query_climate_database(country, year_begin, year_end, month):
    """
    This function creates a dataframe of temperatures for stations in a country
    for a given month and years from the climate database
    
    Inputs:
    country - the country to look in
    year_begin - the first year to gather data for
    year_end - the last year to gather data for
    month - the number of the month of tempterature to look at
    
    Outputs a dataframe according to the specifications
    """
    
    #The command pulls data from all three tables by joining them
    cmd = """
    SELECT S.name, S.latitude, S.longitude, C.country, T.year, T.month, T.temp
    FROM temperatures T
    LEFT JOIN stations S ON T.id = S.id
    LEFT JOIN countries C ON C.FIPS = S.FIPS
    WHERE C.country= \"""" + str(country) + """\"
    AND T.year >=""" + str(year_begin) + """
    AND T.year <=""" + str(year_end) + """
    AND T.month =""" + str(month)
    
    #Open the connection to execute the command
    conn = sqlite3.connect("climate.db")
    df = pd.read_sql_query(cmd, conn)
    conn.close()
    return df

Lets do an example where we look at temperatures in December for stations in Egypt from 2009 to 2012.

In [52]:
query_climate_database("Egypt", 2009, 2012, 12).head()

NAME  LATITUDE  LONGITUDE Country  Year  Month   Temp
0  MERSA_MATRUH   31.3331    27.2167   Egypt  2009     12  16.69
1  MERSA_MATRUH   31.3331    27.2167   Egypt  2010     12  15.90
2        ASSWAN   23.9667    32.7831   Egypt  2009     12  18.90
3        ASSWAN   23.9667    32.7831   Egypt  2010     12  19.50
4          SIWA   29.2000    25.3167   Egypt  2010     12  14.50

## 3 Write a Geographic Scatter Function for Yearly Temperature Increases

Our next task is to create a function our query that will create a figure to address the following question:

*How does the average yearly change in temperature vary within a given country?*

To do this we are going to group the data by station and find the change using linear regression. For this we will need a function to use in the apply.

In [4]:
from sklearn.linear_model import LinearRegression

def coef(data_group):
    """
    This function finds the linear regression equation for a data group
    
    Input: data_group - as data group from the groupby function
    
    Output the rounded first coefficient of the equation
    """
    x = data_group[["Year"]]
    y = data_group["Temp"]
    LR = LinearRegression()
    LR.fit(x,y)
    return round(LR.coef_[0],3)

For labeling we will want to convert numbers to months so let's create a key

In [18]:
months = {1: "January",
          2: "February",
          3: "March",
          4: "April",
          5: "May",
          6: "June",
          7: "July",
          8: "August",
          9: "September",
          10: "October",
          11: "November",
          12: "December"}

We make this figure with plotly.

In [5]:
from plotly import express as px

We will create a function that will plot stations in a country to graphically show how temperatures are changing

In [42]:
def temperature_coefficient_plot(country, year_begin, year_end, month, min_obs, **kwargs):
    """
    This function will create a figure showing the locations of each station in a country, 
    colored by the estimated yearly temperature increase according to the user's specifictions
    
    Inputs:
        country - the country to plot the stations from
        year_begin - the first year to consider
        year_end - the last year to consider
        month - the number of the month whose temperature to look at
        min_obs - the minimum number of observations for a station
        **kwargs - user specified plot arguments
        
    Outputs a figure
    """
    #Use our previous function to gather the data
    df = query_climate_database(country, year_begin, year_end, month)
    
    #Get count of observations
    obs = df.groupby(["NAME"])["Month"].transform(np.sum) / month
    
    #Filter out stations with too few observations
    df = df[obs >= min_obs]
    df = df.reset_index()
    
    #Apply coef function from above
    coefs = df.groupby(["NAME", "LATITUDE", "LONGITUDE"]).apply(coef).reset_index()
    coefs = coefs.rename(columns = {0: "Est. Yearly<br>Increase (" + u'\N{DEGREE SIGN}' + "C)"})
    
    title = "Estimates of Yearly Temperature Increase in " + months[month]
    title += " for Stations in " + country +", years "+ str(year_begin) + "-" + str(year_end)
    
    fig = px.scatter_mapbox(coefs,
                            lat = "LATITUDE",
                            lon = "LONGITUDE",
                            color = "Est. Yearly<br>Increase (" + u'\N{DEGREE SIGN}' + "C)",
                            #0, #This is the coef column
                            color_continuous_midpoint = 0, #Center colorbar
                            hover_name = "NAME",
                            title = title, 
                            mapbox_style = "stamen-terrain",
                            **kwargs)
    #fig.layout.coloraxis.colorbar.title = "Est. Yearly<br>Increase (" + u'\N{DEGREE SIGN}' + "C)"
    return fig


Now we'll look at an example with Germany

In [43]:
fig = temperature_coefficient_plot("Germany", 1990, 2020, 8, 
                                   min_obs = 15,
                                   zoom = 4,
                                   color_continuous_scale=px.colors.diverging.RdGy_r)

fig.show()

In order to get the plot to appear on our blot, we will save it as an html file

In [46]:
from plotly.io import write_html
write_html(fig, "plot3.html")

## 4 Temperature by Latitude

For this plot we want to answer the question

*How does temperature vary by latitude and what impact does elevation have?*

This time we are going to make use of more function in SQL, where we can actually do all of the preprocessing of the data.

Using a similar process as last time, we are going to select the information about a station and it's location from the temperatures table joined with stations and countries. But this time we are going to use a GROUP BY statement to group all the years and months together for each station name. Then in the SELECT statement, we can take the average temperature. We are also renaming the elevation variable here so it clearer. In the WHERE statement, which is before the data is grouped, we exclude some observations with an elevation of 9999, as this data error would mess up our plot. Lastly, we use a HAVING statement, which applies after the GROUP BY, to only include rows with the minimum number of observations.

In [127]:
def query_average_temps(year_begin, year_end, min_obs):
    """
    This function uses the climate database to create a dataframe of 
    average temperatures within the given years for each station, 
    providing it has sufficient observations
    
    Inputs:
    year_begin - the first year to gather data for
    year_end - the last year to gather data for
    min_obs - the minimum number of months of observation the station must have
    
    Outputs a dataframe according to the specifications
    """
        
    cmd = """
    SELECT S.name, C.country, S.latitude, S.longitude,
        S.stnelev as "Elevation (m)", ROUND(AVG(T.temp),2) as Temperature
    FROM temperatures T
    LEFT JOIN stations S ON T.id = S.id
    LEFT JOIN countries C ON C.FIPS = S.FIPS 
    WHERE T.year >=""" + str(year_begin) + """
    AND T.year <=""" + str(year_end) + """
    AND S.stnelev NOT IN (9999)
    GROUP BY S.name
    HAVING COUNT(T.temp) >= """ + str(min_obs)

    conn = sqlite3.connect("climate.db")
    df = pd.read_sql_query(cmd, conn)
    conn.close()
    return df

Let's look at the table for average temperatures between 2011 and 2019 with a minimum of 20 observations

In [128]:
query_average_temps(2011, 2019, 20).head()

NAME        Country  LATITUDE  LONGITUDE  \
0        100_MILE_HOUSE_6NE         Canada   51.6833  -121.2167   
1  108_MILE_HOUSE_ABEL_LAKE         Canada   51.7000  -121.4000   
2              3_MILE_IDAHO  United States   44.3958  -112.1081   
3    83_MONUMENT_WASHINGTON  United States   49.0017  -120.6475   
4                   A12_CPP    Netherlands   55.3992     3.8103   

   Elevation (m)  Temperature  
0          928.0         4.42  
1          994.0         5.87  
2         2019.3         5.70  
3         1979.4         2.33  
4           48.0        10.23

Now we'll write the function that will make the scatterplot. Since we already preprocessed the dataframe in the SQL query, all we need to do is run that function and make the figure

In [136]:
def temp_lat_plot(year_begin, year_end, min_obs, **kwargs):
    """
    This function plots the average temperature versus the latitude for
    each station, colored by the elevation.
    
    Inputs:
    year_begin - the first year to gather data for
    year_end - the last year to gather data for
    min_obs - the minimum number of months of observation the station must have
    **kwargs - any additional plotting arguments
    
    Outputs a scatterplot according to the specifications
    """
    #Get data
    df = query_average_temps(year_begin, year_end, min_obs)
    
    title = "Temperature versus latitude and elevation from " + str(year_begin)
    title += " to " + str(year_end)
    
    #Make figure
    fig = px.scatter(df,
                     x = "LATITUDE",
                     y = "Temperature",
                     color = "Elevation (m)",
                     title = title,
                     hover_name = "NAME",
                     hover_data = ["Country"], #Added info
                     **kwargs)
    return fig

For an example, lets look at the past 30 years

In [137]:
temp_lat_plot(1990, 2020, 100,
              color_continuous_scale = "sunset" # Makes high elevation darker
             )

### 5 Seasonal differences by climate zone and hemisphere

The third and final question we want to answer is:

*How do climate zones affect seasonal differences in the northern and southern hemispheres?*

To do this we will once again make a query function. This will be similar to the one last time, with the addition of creating new variacles. We will use CASE within the SELECT statement to use latitude to classify the climate zones and hemispheres

In [163]:
def query_zoning(year_begin, year_end, min_obs):
    """
    This function uses the climate database to create a dataframe of 
    average temperatures within the given years for each month at 
    each station, providing it has sufficient observations, and 
    creates new columns for climate zone and hemisphere
    
    Inputs:
    year_begin - the first year to gather data for
    year_end - the last year to gather data for
    min_obs - the minimum number of months of observation the station must have
    
    Outputs a dataframe according to the specifications
    """
    
    cmd = """
    SELECT S.Name, C.country, S.latitude,
        CASE
            WHEN S.latitude > 60 OR S.latitude < -60 THEN "arctic"
            WHEN S.latitude > 30 OR S.latitude < -30 THEN "temperate"
            ELSE "tropics"
            END AS zone,
        CASE
            WHEN S.latitude > 0 THEN "northern"
            ELSE "southern"
            END AS hemisphere,
       T.month, AVG(T.temp) as Temp, COUNT(T.temp) as count
    FROM temperatures T
    LEFT JOIN stations S ON T.id = S.id
    LEFT JOIN countries C ON C.FIPS = S.FIPS 
    WHERE T.year >=""" + str(year_begin) + """
    AND T.year <=""" + str(year_end) + """
    AND S.stnelev NOT IN (9999)
    GROUP BY S.name, T.month
    HAVING COUNT(T.temp) >= """ + str(min_obs)

    conn = sqlite3.connect("climate.db")
    df = pd.read_sql_query(cmd, conn)
    conn.close()
    return df

Lets look at the resulting dataframe from 1940 to 1950 with 10 observations

In [164]:
query_zoning(1940,1950,10).head()

NAME  Country  LATITUDE       zone hemisphere  Month       Temp  count
0  AACHEN  Germany   50.7839  temperate   northern      1   0.032727     11
1  AACHEN  Germany   50.7839  temperate   northern      2   2.050909     11
2  AACHEN  Germany   50.7839  temperate   northern      3   5.855455     11
3  AACHEN  Germany   50.7839  temperate   northern      4  10.242727     11
4  AACHEN  Germany   50.7839  temperate   northern      5  13.280000     11

Next we will make the plot. Here the user will be able to specify the months they want to compare. To allow this, we will use create a separate data frame for each of the two months and then inner join them, so we only have observations with temperatures for both months. Then we can easily find the difference.

We will make a multi faceted violin plot so we can see the distribution of temperatures within each zone.

In [166]:
def zone_violin_plot(year_begin, year_end, min_obs, month1, month2, **kwargs):
    """
    This function makes a violin plot of the difference in average temperature 
    between two specified months. The graph is multi-faceted by hemisphere and
    has separate plots for each climate zone.
    
    Inputs:
    year_begin - the first year to gather data for
    year_end - the last year to gather data for
    min_obs - the minimum number of months of observation the station must have
    **kwargs - any additional plotting arguments
    
    Outputs a multifaceted violin plot according to the specifications
    """
    df = query_zoning(year_begin, year_end, min_obs)
    m1 = df[df["Month"]==month1]
    m2 = df[df["Month"]==month2]
    df = pd.merge(m1, m2, on = ["NAME", "Country", "zone","hemisphere", "LATITUDE"])
    df["Difference"] = df["Temp_x"] - df["Temp_y"]
    title = "Temperature difference between " + months[month1] + " and "
    title += months[month2] + " by climate zone and hemisphere"
    fig = px.violin(df,
                    x = "Difference",
                    color = "zone",
                    facet_row = "hemisphere",
                    title = title,
                    hover_name = "NAME",
                    hover_data = ["Country", "LATITUDE"],
                    category_orders = {"zone": ["tropics", "temperate", "arctic"]},
                    **kwargs)
    return fig
    

Now lets use this to look at the difference in average temperatures between January and July over the entirity of our data

In [168]:
fig = zone_violin_plot(1901, 2020, 20, 1, 7)
fig.show()